In [ ]:
!python setup.py install

python3: can't open file 'setup.py': [Errno 2] No such file or directory


In [ ]:
import six
import sys
sys.modules['sklearn.externals.six'] = six

Importing Packages

In [ ]:
import pandas as pd
import numpy as np
import xgboost as xgb
from pandas_profiling import ProfileReport
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
#EDA
from collections import Counter
import pandas_profiling as pp

In [ ]:
!pip install 'neptune-contrib[monitoring]>=0.24.9'

In [ ]:
from sklearn.preprocessing import StandardScaler
# data splitting
from sklearn.model_selection import train_test_split
# data modeling
from sklearn.metrics import confusion_matrix,accuracy_score,roc_curve,classification_report
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import GaussianNB
from xgboost import XGBClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import SVC
#ensembling
from mlxtend.classifier import StackingCVClassifier
from neptunecontrib.monitoring.xgboost_monitor import neptune_callback

/usr/local/lib/python3.7/dist-packages/neptunecontrib/monitoring/xgboost_monitor.py:21: UserWarning: neptunecontrib.monitoring.xgboost_monitor was moved to neptunecontrib.monitoring.xgboost
neptunecontrib.monitoring.xgboost_monitor will be removed in future releases.

  warnings.warn(message)


In [ ]:
import six
import sys
sys.modules['sklearn.externals.six'] = six

In [ ]:
! pip install https://github.com/pandas-profiling/pandas-profiling/archive/master.zip 


  Using cached https://github.com/pandas-profiling/pandas-profiling/archive/master.zip (25.9 MB)


Loading Datasets

In [ ]:
from google.colab import files
uploaded = files.upload()

Saving framingham.csv to framingham.csv


In [ ]:
df = pd.read_csv("framingham.csv")
df.head()


male  age  education  currentSmoker  cigsPerDay  BPMeds  prevalentStroke  \
0     1   39        4.0              0         0.0     0.0                0   
1     0   46        2.0              0         0.0     0.0                0   
2     1   48        1.0              1        20.0     0.0                0   
3     0   61        3.0              1        30.0     0.0                0   
4     0   46        3.0              1        23.0     0.0                0   

   prevalentHyp  diabetes  totChol  sysBP  diaBP    BMI  heartRate  glucose  \
0             0         0    195.0  106.0   70.0  26.97       80.0     77.0   
1             0         0    250.0  121.0   81.0  28.73       95.0     76.0   
2             0         0    245.0  127.5   80.0  25.34       75.0     70.0   
3             1         0    225.0  150.0   95.0  28.58       65.0    103.0   
4             0         0    285.0  130.0   84.0  23.10       85.0     85.0   

   TenYearCHD  
0           0  
1           0  
2           0  
3           1  
4           0

In [ ]:
df = df.fillna(0)

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4238 entries, 0 to 4237
Data columns (total 16 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   male             4238 non-null   int64  
 1   age              4238 non-null   int64  
 2   education        4238 non-null   float64
 3   currentSmoker    4238 non-null   int64  
 4   cigsPerDay       4238 non-null   float64
 5   BPMeds           4238 non-null   float64
 6   prevalentStroke  4238 non-null   int64  
 7   prevalentHyp     4238 non-null   int64  
 8   diabetes         4238 non-null   int64  
 9   totChol          4238 non-null   float64
 10  sysBP            4238 non-null   float64
 11  diaBP            4238 non-null   float64
 12  BMI              4238 non-null   float64
 13  heartRate        4238 non-null   float64
 14  glucose          4238 non-null   float64
 15  TenYearCHD       4238 non-null   int64  
dtypes: float64(9), int64(7)
memory usage: 529.9 KB


EDA

In [ ]:
pp.ProfileReport(df)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Model Preparation

In [ ]:
y = df["TenYearCHD"]
X = df.drop('TenYearCHD',axis=1)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state = 0)

In [ ]:
print(y_test.unique())
Counter(y_train)

[0 1]


Counter({0: 2884, 1: 506})

In [ ]:
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

ML Model

In [ ]:
m1 = 'Logistic Regression'
lr = LogisticRegression()
model = lr.fit(X_train, y_train)
lr_predict = lr.predict(X_test)
lr_conf_matrix = confusion_matrix(y_test, lr_predict)
lr_acc_score = accuracy_score(y_test, lr_predict)
print("confussion matrix")
print(lr_conf_matrix)
print("\n")
print("Accuracy of Logistic Regression:",lr_acc_score*100,'\n')
print(classification_report(y_test,lr_predict))

confussion matrix
[[708   2]
 [130   8]]


Accuracy of Logistic Regression: 84.43396226415094 

              precision    recall  f1-score   support

           0       0.84      1.00      0.91       710
           1       0.80      0.06      0.11       138

    accuracy                           0.84       848
   macro avg       0.82      0.53      0.51       848
weighted avg       0.84      0.84      0.78       848



In [ ]:
m2 = 'Naive Bayes'
nb = GaussianNB()
nb.fit(X_train,y_train)
nbpred = nb.predict(X_test)
nb_conf_matrix = confusion_matrix(y_test, nbpred)
nb_acc_score = accuracy_score(y_test, nbpred)
print("confussion matrix")
print(nb_conf_matrix)
print("\n")
print("Accuracy of Naive Bayes model:",nb_acc_score*100,'\n')
print(classification_report(y_test,nbpred))

confussion matrix
[[663  47]
 [106  32]]


Accuracy of Naive Bayes model: 81.95754716981132 

              precision    recall  f1-score   support

           0       0.86      0.93      0.90       710
           1       0.41      0.23      0.29       138

    accuracy                           0.82       848
   macro avg       0.63      0.58      0.60       848
weighted avg       0.79      0.82      0.80       848



In [ ]:
m3 = 'Random Forest Classfier'
rf = RandomForestClassifier(n_estimators=20, random_state=12,max_depth=5)
rf.fit(X_train,y_train)
rf_predicted = rf.predict(X_test)
rf_conf_matrix = confusion_matrix(y_test, rf_predicted)
rf_acc_score = accuracy_score(y_test, rf_predicted)
print("confussion matrix")
print(rf_conf_matrix)
print("\n")
print("Accuracy of Random Forest:",rf_acc_score*100,'\n')
print(classification_report(y_test,rf_predicted))

confussion matrix
[[710   0]
 [135   3]]


Accuracy of Random Forest: 84.08018867924528 

              precision    recall  f1-score   support

           0       0.84      1.00      0.91       710
           1       1.00      0.02      0.04       138

    accuracy                           0.84       848
   macro avg       0.92      0.51      0.48       848
weighted avg       0.87      0.84      0.77       848



In [ ]:
m5 = 'K-NeighborsClassifier'
knn = KNeighborsClassifier(n_neighbors=10)
knn.fit(X_train, y_train)
knn_predicted = knn.predict(X_test)
knn_conf_matrix = confusion_matrix(y_test, knn_predicted)
knn_acc_score = accuracy_score(y_test, knn_predicted)
print("confussion matrix")
print(knn_conf_matrix)
print("\n")
print("Accuracy of K-NeighborsClassifier:",knn_acc_score*100,'\n')
print(classification_report(y_test,knn_predicted))

confussion matrix
[[709   1]
 [136   2]]


Accuracy of K-NeighborsClassifier: 83.84433962264151 

              precision    recall  f1-score   support

           0       0.84      1.00      0.91       710
           1       0.67      0.01      0.03       138

    accuracy                           0.84       848
   macro avg       0.75      0.51      0.47       848
weighted avg       0.81      0.84      0.77       848



In [ ]:
m6 = 'DecisionTreeClassifier'
dt = DecisionTreeClassifier(criterion = 'entropy',random_state=0,max_depth = 6)
dt.fit(X_train, y_train)
dt_predicted = dt.predict(X_test)
dt_conf_matrix = confusion_matrix(y_test, dt_predicted)
dt_acc_score = accuracy_score(y_test, dt_predicted)
print("confussion matrix")
print(dt_conf_matrix)
print("\n")
print("Accuracy of DecisionTreeClassifier:",dt_acc_score*100,'\n')
print(classification_report(y_test,dt_predicted))

confussion matrix
[[696  14]
 [132   6]]


Accuracy of DecisionTreeClassifier: 82.78301886792453 

              precision    recall  f1-score   support

           0       0.84      0.98      0.91       710
           1       0.30      0.04      0.08       138

    accuracy                           0.83       848
   macro avg       0.57      0.51      0.49       848
weighted avg       0.75      0.83      0.77       848



In [ ]:
m7 = 'Support Vector Classifier'
svc =  SVC(kernel='rbf', C=2)
svc.fit(X_train, y_train)
svc_predicted = svc.predict(X_test)
svc_conf_matrix = confusion_matrix(y_test, svc_predicted)
svc_acc_score = accuracy_score(y_test, svc_predicted)
print("confussion matrix")
print(svc_conf_matrix)
print("\n")
print("Accuracy of Support Vector Classifier:",svc_acc_score*100,'\n')
print(classification_report(y_test,svc_predicted))

confussion matrix
[[705   5]
 [129   9]]


Accuracy of Support Vector Classifier: 84.19811320754717 

              precision    recall  f1-score   support

           0       0.85      0.99      0.91       710
           1       0.64      0.07      0.12       138

    accuracy                           0.84       848
   macro avg       0.74      0.53      0.52       848
weighted avg       0.81      0.84      0.78       848



## ANN Multilayer Perceptron Classifier







In [ ]:
from sklearn.metrics import make_scorer, accuracy_score
from sklearn.model_selection import GridSearchCV
from sklearn.neural_network import MLPClassifier

In [ ]:
ann_clf = MLPClassifier()

#Parameters
parameters = {'solver': ['lbfgs'],
             'alpha':[1e-4],
             'hidden_layer_sizes':(9,14,14,2),   # 9 input, 14-14 neuron in 2 layers,1 output layer
             'random_state': [1]}

In [ ]:
# Type of scoring to compare parameter combos 
acc_scorer = make_scorer(accuracy_score)

# Run grid search 
grid_obj = GridSearchCV(ann_clf, parameters, scoring=acc_scorer)
grid_obj = grid_obj.fit(X_train, y_train)

# Pick the best combination of parameters
ann_clf = grid_obj.best_estimator_

In [ ]:
# Fit the best algorithm to the data 
ann_clf.fit(X_train, y_train)

MLPClassifier(hidden_layer_sizes=2, random_state=1, solver='lbfgs')

In [ ]:
MLPClassifier(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
       beta_2=0.999, early_stopping=False, epsilon=1e-08,
       hidden_layer_sizes=14, learning_rate='constant',
       learning_rate_init=0.001, max_iter=200, momentum=0.9,
       nesterovs_momentum=True, power_t=0.5, random_state=1, shuffle=True,
       solver='lbfgs', tol=0.0001, validation_fraction=0.1, verbose=False,
       warm_start=False)

MLPClassifier(hidden_layer_sizes=14, random_state=1, solver='lbfgs')

In [ ]:
y_pred_ann = ann_clf.predict(X_test)

In [ ]:
from sklearn.metrics import confusion_matrix
cm_ann = confusion_matrix(y_test, y_pred_ann)
cm_ann

array([[703,   7],
       [127,  11]])

In [ ]:
ann_result = accuracy_score(y_test,y_pred_ann)
print(classification_report(y_test,y_pred_ann))
# mlp.fit(X_train, y_train)
# mlp_predicted = svc.predict(X_test)
# mlp_conf_matrix = confusion_matrix(y_test, svc_predicted)
# mlp_acc_score = accuracy_score(y_test, svc_predicted)
print("confussion matrix")
# print(mlp_conf_matrix)
print("\n")
# print("Accuracy of Multi Layer Perceptron:",mlp_acc_score*100,'\n')
# print(classification_report(y_test,mlp_predicted))
ann_result

              precision    recall  f1-score   support

           0       0.85      0.99      0.91       710
           1       0.61      0.08      0.14       138

    accuracy                           0.84       848
   macro avg       0.73      0.53      0.53       848
weighted avg       0.81      0.84      0.79       848

confussion matrix




0.8419811320754716

In [ ]:
recall_ann = cm_ann[0][0]/(cm_ann[0][0] + cm_ann[0][1])
precision_ann = cm_ann[0][0]/(cm_ann[0][0]+cm_ann[1][1])
recall_ann,precision_ann

(0.9901408450704225, 0.9845938375350141)